# IBM's Applied Data Science Capstone Project :Battle of Neighborhoods

## Where to Stay for the Best Culinary Experience in Montreal

### Introduction & Business Problem
Food has always been a staple to humans and is also considered an art form. The culinary world offers a different variety of cuisines that can leave you speechless after one bite. However, in this modern age, there are various restaurants that are disperse all around a city. 

What if we can locate the best neighborhood/geographical location where tourist, clients, hotel owners, etc. can know that they are at the premium spot where they will be offered the upmost culinary experience.

For this project, the focus will be on the city of Montreal which is one the most ethnically and culturally diverse cities in the world. In the following notebook, the exploration of the different neighborhoods of Montreal and find out, which neighborhood to be at to experience the best culinary experience possible.


### Data Section
To start of the future research, the data of the Montreal neighborhoods will be needed. The Postal Code of the Montreal Neighborhoods can be found here: https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_H

 After cleaning up the data, the geolocator API will be used to find the coordinate of the different postal codes in Montreal. 
 
Once the coordinates are found, the FourSquare API will be used to analyze the different neighborhoods to find the ideal location to stay to have the best culinary experience in Montreal. 

At this point in time, I don’t have any other datasets to enhance the analysis, however, as the CAPSTONE continues, there will be hopefully another dataset and/or API that will be used to furthermore complete the research.


In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [2]:
import urllib.request
import numpy as np
from bs4 import BeautifulSoup
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_H"

page = urllib.request.urlopen(url)

soup = BeautifulSoup(page,"lxml")

In [3]:
print(soup.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   List of postal codes of Canada: H - Wikipedia
  </title>
  <script>
   document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"aac12778-35b6-49c5-b4aa-1a1f739717ab","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_postal_codes_of_Canada:_H","wgTitle":"List of postal codes of Canada: H","wgCurRevisionId":955302134,"wgRevisionId":955302134,"wgArticleId":576883,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Articles with short description","Communications in Quebec","Postal codes in Canada","Dollar

In [4]:
soup.title.string

'List of postal codes of Canada: H - Wikipedia'

In [5]:
my_table = soup.find('table')

In [6]:
print(my_table)


<table cellpadding="2" cellspacing="0" rules="all" style="border-collapse: collapse; border: 1px solid #ccc;" width="100%">
<tbody><tr>
<td style="color: #CCCCCC;" valign="top" width="11%">
<p><b>H0A,</b><br/><span style="font-size:80%;"><i>Not assigned</i></span>
</p>
</td>
<td valign="top" width="11%">
<p><b>H1A</b><br/><span style="font-size:80%;"><a href="/wiki/Pointe-aux-Trembles" title="Pointe-aux-Trembles">Pointe-aux-Trembles</a></span>
</p>
</td>
<td valign="top" width="11%">
<p><b>H2A,</b><br/><span style="font-size:80%;"><a class="mw-redirect" href="/wiki/Saint-Michel_district,_Quebec" title="Saint-Michel district, Quebec">Saint-Michel,</a><br/>East</span>
</p>
</td>
<td valign="top" width="11%">
<p><b>H3A</b><br/><span style="font-size:80%;"><a href="/wiki/Downtown_Montreal" title="Downtown Montreal">Downtown Montreal</a><br/> North<br/>(<a href="/wiki/McGill_University" title="McGill University">McGill University</a>)</span>
</p>
</td>
<td valign="top" width="11%">
<p><b>H4

In [7]:
links=my_table.findAll('a')

In [8]:
links

[<a href="/wiki/Pointe-aux-Trembles" title="Pointe-aux-Trembles">Pointe-aux-Trembles</a>,
 <a class="mw-redirect" href="/wiki/Saint-Michel_district,_Quebec" title="Saint-Michel district, Quebec">Saint-Michel,</a>,
 <a href="/wiki/Downtown_Montreal" title="Downtown Montreal">Downtown Montreal</a>,
 <a href="/wiki/McGill_University" title="McGill University">McGill University</a>,
 <a class="mw-redirect" href="/wiki/Notre-Dame-de-Gr%C3%A2ce,_Quebec" title="Notre-Dame-de-Grâce, Quebec">Notre-Dame-de-Grâce</a>,
 <a href="/wiki/Place_Bonaventure" title="Place Bonaventure">Place Bonaventure</a>,
 <a class="mw-redirect" href="/wiki/Duvernay-Est,_Quebec" title="Duvernay-Est, Quebec">Duvernay-Est</a>,
 <a href="/wiki/Dollard-des-Ormeaux" title="Dollard-des-Ormeaux">Dollard-des-<br/>Ormeaux</a>,
 <a class="mw-redirect" href="/wiki/Montreal_East,_Quebec" title="Montreal East, Quebec">Montreal East</a>,
 <a class="mw-redirect" href="/wiki/Ahuntsic,_Quebec" title="Ahuntsic, Quebec">Ahuntsic</a>,
 <

In [9]:
neighborhoods = []
for link in links:
    neighborhoods.append(str(link.get('title')))
    
print(neighborhoods)

['Pointe-aux-Trembles', 'Saint-Michel district, Quebec', 'Downtown Montreal', 'McGill University', 'Notre-Dame-de-Grâce, Quebec', 'Place Bonaventure', 'Duvernay-Est, Quebec', 'Dollard-des-Ormeaux', 'Montreal East, Quebec', 'Ahuntsic, Quebec', 'Downtown Montreal', 'Notre-Dame-de-Grâce, Quebec', 'Place Desjardins', 'Saint-François, Laval, Quebec', 'Dollard-des-Ormeaux', 'Rivière-des-Prairies', 'Ahuntsic, Quebec', 'Griffintown, Quebec', 'Île Notre-Dame', 'Île Sainte-Hélène', 'Université de Montréal', 'Saint-Henri, Montreal', 'Saint-Vincent-de-Paul, Quebec', "L'Île-Bizard, Quebec", 'Rivière-des-Prairies', 'Villeray, Quebec', "L'Île-Des-Soeurs, Quebec", 'Ville Émard, Quebec', 'Duvernay, Quebec', "L'Île-Bizard, Quebec", 'Montréal-Nord', 'Petite-Patrie, Quebec', 'Downtown Montreal', 'Concordia University (Montreal)', 'Verdun, Quebec', 'Pont-Viau, Quebec', 'Dollard-des-Ormeaux', 'Postal codes in Canada', 'Montréal-Nord', 'The Plateau', 'Downtown Montreal', 'Verdun, Quebec', 'Auteuil, Quebec', 

In [10]:
postalcode = my_table.findAll('b')

In [11]:
postalcode

[<b>H0A,</b>,
 <b>H1A</b>,
 <b>H2A,</b>,
 <b>H3A</b>,
 <b>H4A</b>,
 <b>H5A</b>,
 <b>H7A</b>,
 <b>H8A</b>,
 <b>H9A</b>,
 <b>H0B</b>,
 <b>H1B</b>,
 <b>H2B</b>,
 <b>H3B</b>,
 <b>H4B</b>,
 <b>H5B</b>,
 <b>H7B</b>,
 <b>H8B</b>,
 <b>H9B</b>,
 <b>H0C</b>,
 <b>H1C</b>,
 <b>H2C</b>,
 <b>H3C</b>,
 <b>H4C</b>,
 <b>H5C</b>,
 <b>H7C</b>,
 <b>H8C</b>,
 <b>H9C</b>,
 <b>H0E</b>,
 <b>H1E</b>,
 <b>H2E</b>,
 <b>H3E</b>,
 <b>H4E</b>,
 <b>H5E</b>,
 <b>H7E</b>,
 <b>H8E</b>,
 <b>H9E</b>,
 <b>H0G</b>,
 <b>H1G</b>,
 <b>H2G</b>,
 <b>H3G</b>,
 <b>H4G</b>,
 <b>H5G</b>,
 <b>H7G</b>,
 <b>H8G</b>,
 <b>H9G</b>,
 <b>H0H</b>,
 <b>Reserved</b>,
 <b>H1H</b>,
 <b>H2H</b>,
 <b>H3H</b>,
 <b>H4H</b>,
 <b>H5H</b>,
 <b>H7H</b>,
 <b>H8H</b>,
 <b>H9H</b>,
 <b>H0J</b>,
 <b>H1J</b>,
 <b>H2J</b>,
 <b>H3J</b>,
 <b>H4J</b>,
 <b>H5J</b>,
 <b>H7J</b>,
 <b>H8J</b>,
 <b>H9J</b>,
 <b>H0K</b>,
 <b>H1K</b>,
 <b>H2K</b>,
 <b>H3K</b>,
 <b>H4K</b>,
 <b>H5K</b>,
 <b>H7K</b>,
 <b>H8K</b>,
 <b>H9K</b>,
 <b>H0L</b>,
 <b>H1L</b>,
 <b>H2L</b>,
 <b>H

In [12]:
postalcodes =[ str(s) for s in postalcode]
print(postalcodes)

['<b>H0A,</b>', '<b>H1A</b>', '<b>H2A,</b>', '<b>H3A</b>', '<b>H4A</b>', '<b>H5A</b>', '<b>H7A</b>', '<b>H8A</b>', '<b>H9A</b>', '<b>H0B</b>', '<b>H1B</b>', '<b>H2B</b>', '<b>H3B</b>', '<b>H4B</b>', '<b>H5B</b>', '<b>H7B</b>', '<b>H8B</b>', '<b>H9B</b>', '<b>H0C</b>', '<b>H1C</b>', '<b>H2C</b>', '<b>H3C</b>', '<b>H4C</b>', '<b>H5C</b>', '<b>H7C</b>', '<b>H8C</b>', '<b>H9C</b>', '<b>H0E</b>', '<b>H1E</b>', '<b>H2E</b>', '<b>H3E</b>', '<b>H4E</b>', '<b>H5E</b>', '<b>H7E</b>', '<b>H8E</b>', '<b>H9E</b>', '<b>H0G</b>', '<b>H1G</b>', '<b>H2G</b>', '<b>H3G</b>', '<b>H4G</b>', '<b>H5G</b>', '<b>H7G</b>', '<b>H8G</b>', '<b>H9G</b>', '<b>H0H</b>', '<b>Reserved</b>', '<b>H1H</b>', '<b>H2H</b>', '<b>H3H</b>', '<b>H4H</b>', '<b>H5H</b>', '<b>H7H</b>', '<b>H8H</b>', '<b>H9H</b>', '<b>H0J</b>', '<b>H1J</b>', '<b>H2J</b>', '<b>H3J</b>', '<b>H4J</b>', '<b>H5J</b>', '<b>H7J</b>', '<b>H8J</b>', '<b>H9J</b>', '<b>H0K</b>', '<b>H1K</b>', '<b>H2K</b>', '<b>H3K</b>', '<b>H4K</b>', '<b>H5K</b>', '<b>H7K</b>'

In [13]:
df = pd.DataFrame()
df['Postal Code'] = postalcodes
#df['Neighborhoods'] = neighborhoods
df['Postal Code'] = df['Postal Code'].map(lambda x: x.lstrip('<b>').rstrip(',<//b>'))


#df=df.reset_index(drop=True)

df

Postal Code
0           H0A
1           H1A
2           H2A
3           H3A
4           H4A
5           H5A
6           H7A
7           H8A
8           H9A
9           H0B
10          H1B
11          H2B
12          H3B
13          H4B
14          H5B
15          H7B
16          H8B
17          H9B
18          H0C
19          H1C
20          H2C
21          H3C
22          H4C
23          H5C
24          H7C
25          H8C
26          H9C
27          H0E
28          H1E
29          H2E
30          H3E
31          H4E
32          H5E
33          H7E
34          H8E
35          H9E
36          H0G
37          H1G
38          H2G
39          H3G
40          H4G
41          H5G
42          H7G
43          H8G
44          H9G
45          H0H
46     Reserved
47          H1H
48          H2H
49          H3H
50          H4H
51          H5H
52          H7H
53          H8H
54          H9H
55          H0J
56          H1J
57          H2J
58          H3J
59          H4J
60          H5J
61          H7J
62          H8J
63          H9J
64          H0K
65          H1K
66          H2K
67          H3K
68          H4K
69          H5K
70          H7K
71          H8K
72          H9K
73          H0L
74          H1L
75          H2L
76          H3L
77          H4L
78          H5L
79          H7L
80          H8L
81          H9L
82          H0M
83          H1M
84          H2M
85          H3M
86          H4M
87          H5M
88          H7M
89          H8M
90          H9M
91          H0N
92          H1N
93          H2N
94          H3N
95          H4N
96          H5N
97          H7N
98          H8N
99          H9N
100         H0P
101         H1P
102         H2P
103         H3P
104         H4P
105         H5P
106         H7P
107         H8P
108         H9P
109         H0R
110         H1R
111         H2R
112         H3R
113         H4R
114         H5R
115         H7R
116         H8R
117         H9R
118         H0S
119         H1S
120         H2S
121         H3S
122         H4S
123         H5S
124         H7S
125         H8S
126         H9S
127         H0T
128         H1T
129         H2T
130         H3T
131         H4T
132         H5T
133         H7T
134         H8T
135         H9T
136         H0V
137         H1V
138         H2V
139         H3V
140         H4V
141         H5V
142         H7V
143         H8V
144         H9V
145         H0W
146         H1W
147         H2W
148         H3W
149         H4W
150         H5W
151         H7W
152         H8W
153         H9W
154         H0X
155         H1X
156         H2X
157         H3X
158         H4X
159         H5X
160         H7X
161         H8X
162         H9X
163         H0Y
164         H1Y
165         H2Y
166         H3Y
167         H4Y
168         H5Y
169         H7Y
170         H8Y
171         H9Y
172         H0Z
173         H1Z
174         H2Z
175         H3Z
176         H4Z
177         H5Z
178         H7Z
179         H8Z
180         H9Z

In [14]:
df1 = pd.DataFrame()
df1['Neighborhoods'] = neighborhoods
df1

Neighborhoods
0                                  Pointe-aux-Trembles
1                        Saint-Michel district, Quebec
2                                    Downtown Montreal
3                                    McGill University
4                          Notre-Dame-de-Grâce, Quebec
5                                    Place Bonaventure
6                                 Duvernay-Est, Quebec
7                                  Dollard-des-Ormeaux
8                                Montreal East, Quebec
9                                     Ahuntsic, Quebec
10                                   Downtown Montreal
11                         Notre-Dame-de-Grâce, Quebec
12                                    Place Desjardins
13                       Saint-François, Laval, Quebec
14                                 Dollard-des-Ormeaux
15                                Rivière-des-Prairies
16                                    Ahuntsic, Quebec
17                                 Griffintown, Quebec
18                                      Île Notre-Dame
19                                   Île Sainte-Hélène
20                              Université de Montréal
21                               Saint-Henri, Montreal
22                       Saint-Vincent-de-Paul, Quebec
23                                L'Île-Bizard, Quebec
24                                Rivière-des-Prairies
25                                    Villeray, Quebec
26                            L'Île-Des-Soeurs, Quebec
27                                 Ville Émard, Quebec
28                                    Duvernay, Quebec
29                                L'Île-Bizard, Quebec
30                                       Montréal-Nord
31                               Petite-Patrie, Quebec
32                                   Downtown Montreal
33                     Concordia University (Montreal)
34                                      Verdun, Quebec
35                                   Pont-Viau, Quebec
36                                 Dollard-des-Ormeaux
37                              Postal codes in Canada
38                                       Montréal-Nord
39                                         The Plateau
40                                   Downtown Montreal
41                                      Verdun, Quebec
42                                     Auteuil, Quebec
43                            Sainte-Geneviève, Quebec
44                                 Pierrefonds, Quebec
45                                       Anjou, Quebec
46                                         The Plateau
47                                    Petite-Bourgogne
48                                Cartierville, Quebec
49                                     Auteuil, Quebec
50                                    Kirkland, Quebec
51                                       Anjou, Quebec
52                                  Centre-Sud, Quebec
53                        Pointe-Saint-Charles, Quebec
54                                Cartierville, Quebec
55                                     Auteuil, Quebec
56                                  Senneville, Quebec
57                                  Mercier (Montreal)
58                                  Centre-Sud, Quebec
59                                    Ahuntsic, Quebec
60                               Saint-Laurent, Quebec
61                                 Sainte-Rose, Quebec
62                                           Akwesasne
63                                  Mercier (Montreal)
64                                    Ahuntsic, Quebec
65                                Cartierville, Quebec
66                               Saint-Laurent, Quebec
67                                      Vimont, Quebec
68                                  Mercier (Montreal)
69                                    Ahuntsic, Quebec
70                              Parc-Extension, Quebec
71                               Saint-Laurent, Quebec
72                        

In [15]:
df1.size


134

### Cleaning the DataFrame

I had to do this to clean the index from the non assigned data from the table. I believe there was an easier way to do it if I knew more on beautiful soup to extract the data carefuly but this was the way I decided to do it to simplify things.

#### Cleaning the Postal Code

In [16]:
df.drop(df.index[[0,7,9,16,18,23,25,27,32,34,36,41,43,45,46,51,53,55,60,62,64,69,71,73,78,80,81,82,87,89,90,91,96,99,100,105,109,114,118,123,127,132,135,136,141,143,144,145,150,152,154,159,161,163,168,171,172,177,178,180]],inplace=True)


In [17]:
df.size

121

In [18]:
df

Postal Code
1           H1A
2           H2A
3           H3A
4           H4A
5           H5A
6           H7A
8           H9A
10          H1B
11          H2B
12          H3B
13          H4B
14          H5B
15          H7B
17          H9B
19          H1C
20          H2C
21          H3C
22          H4C
24          H7C
26          H9C
28          H1E
29          H2E
30          H3E
31          H4E
33          H7E
35          H9E
37          H1G
38          H2G
39          H3G
40          H4G
42          H7G
44          H9G
47          H1H
48          H2H
49          H3H
50          H4H
52          H7H
54          H9H
56          H1J
57          H2J
58          H3J
59          H4J
61          H7J
63          H9J
65          H1K
66          H2K
67          H3K
68          H4K
70          H7K
72          H9K
74          H1L
75          H2L
76          H3L
77          H4L
79          H7L
83          H1M
84          H2M
85          H3M
86          H4M
88          H7M
92          H1N
93          H2N
94          H3N
95          H4N
97          H7N
98          H8N
101         H1P
102         H2P
103         H3P
104         H4P
106         H7P
107         H8P
108         H9P
110         H1R
111         H2R
112         H3R
113         H4R
115         H7R
116         H8R
117         H9R
119         H1S
120         H2S
121         H3S
122         H4S
124         H7S
125         H8S
126         H9S
128         H1T
129         H2T
130         H3T
131         H4T
133         H7T
134         H8T
137         H1V
138         H2V
139         H3V
140         H4V
142         H7V
146         H1W
147         H2W
148         H3W
149         H4W
151         H7W
153         H9W
155         H1X
156         H2X
157         H3X
158         H4X
160         H7X
162         H9X
164         H1Y
165         H2Y
166         H3Y
167         H4Y
169         H7Y
170         H8Y
173         H1Z
174         H2Z
175         H3Z
176         H4Z
179         H8Z

#### Cleaning the Neighborhood data

Looking at the data table and the dataframe, there are discrepancies between them because I made beautifulsoup extract links and their are multiple links in the table. I have decided to clean this by manually removing the rows in **df1**

In [19]:
df1.drop(df1.index[[3,18,19,20,33,37,44,62,87,95,117,128]],inplace=True)
df1.size

122

In [20]:
df1

Neighborhoods
0                                  Pointe-aux-Trembles
1                        Saint-Michel district, Quebec
2                                    Downtown Montreal
4                          Notre-Dame-de-Grâce, Quebec
5                                    Place Bonaventure
6                                 Duvernay-Est, Quebec
7                                  Dollard-des-Ormeaux
8                                Montreal East, Quebec
9                                     Ahuntsic, Quebec
10                                   Downtown Montreal
11                         Notre-Dame-de-Grâce, Quebec
12                                    Place Desjardins
13                       Saint-François, Laval, Quebec
14                                 Dollard-des-Ormeaux
15                                Rivière-des-Prairies
16                                    Ahuntsic, Quebec
17                                 Griffintown, Quebec
21                               Saint-Henri, Montreal
22                       Saint-Vincent-de-Paul, Quebec
23                                L'Île-Bizard, Quebec
24                                Rivière-des-Prairies
25                                    Villeray, Quebec
26                            L'Île-Des-Soeurs, Quebec
27                                 Ville Émard, Quebec
28                                    Duvernay, Quebec
29                                L'Île-Bizard, Quebec
30                                       Montréal-Nord
31                               Petite-Patrie, Quebec
32                                   Downtown Montreal
34                                      Verdun, Quebec
35                                   Pont-Viau, Quebec
36                                 Dollard-des-Ormeaux
38                                       Montréal-Nord
39                                         The Plateau
40                                   Downtown Montreal
41                                      Verdun, Quebec
42                                     Auteuil, Quebec
43                            Sainte-Geneviève, Quebec
45                                       Anjou, Quebec
46                                         The Plateau
47                                    Petite-Bourgogne
48                                Cartierville, Quebec
49                                     Auteuil, Quebec
50                                    Kirkland, Quebec
51                                       Anjou, Quebec
52                                  Centre-Sud, Quebec
53                        Pointe-Saint-Charles, Quebec
54                                Cartierville, Quebec
55                                     Auteuil, Quebec
56                                  Senneville, Quebec
57                                  Mercier (Montreal)
58                                  Centre-Sud, Quebec
59                                    Ahuntsic, Quebec
60                               Saint-Laurent, Quebec
61                                 Sainte-Rose, Quebec
63                                  Mercier (Montreal)
64                                    Ahuntsic, Quebec
65                                Cartierville, Quebec
66                               Saint-Laurent, Quebec
67                                      Vimont, Quebec
68                                  Mercier (Montreal)
69                                    Ahuntsic, Quebec
70                              Parc-Extension, Quebec
71                               Saint-Laurent, Quebec
72                                   Laval-des-Rapides
73                                     LaSalle, Quebec
74                               Saint-Léonard, Quebec
75                                    Villeray, Quebec
76                                 Mount Royal, Quebec
77                                 Mount Royal, Quebec
78                                  Fabreville, Quebec
79                                     LaSalle, Quebec
80                        

We now have to reset index of both data frames then combine them together.

In [21]:
df=df.reset_index(drop=True)
df1=df1.reset_index(drop=True)

In [22]:
df['Neighborhoods']=df1['Neighborhoods']

In [23]:
df

Postal Code                                      Neighborhoods
0           H1A                                Pointe-aux-Trembles
1           H2A                      Saint-Michel district, Quebec
2           H3A                                  Downtown Montreal
3           H4A                        Notre-Dame-de-Grâce, Quebec
4           H5A                                  Place Bonaventure
5           H7A                               Duvernay-Est, Quebec
6           H9A                                Dollard-des-Ormeaux
7           H1B                              Montreal East, Quebec
8           H2B                                   Ahuntsic, Quebec
9           H3B                                  Downtown Montreal
10          H4B                        Notre-Dame-de-Grâce, Quebec
11          H5B                                   Place Desjardins
12          H7B                      Saint-François, Laval, Quebec
13          H9B                                Dollard-des-Ormeaux
14          H1C                               Rivière-des-Prairies
15          H2C                                   Ahuntsic, Quebec
16          H3C                                Griffintown, Quebec
17          H4C                              Saint-Henri, Montreal
18          H7C                      Saint-Vincent-de-Paul, Quebec
19          H9C                               L'Île-Bizard, Quebec
20          H1E                               Rivière-des-Prairies
21          H2E                                   Villeray, Quebec
22          H3E                           L'Île-Des-Soeurs, Quebec
23          H4E                                Ville Émard, Quebec
24          H7E                                   Duvernay, Quebec
25          H9E                               L'Île-Bizard, Quebec
26          H1G                                      Montréal-Nord
27          H2G                              Petite-Patrie, Quebec
28          H3G                                  Downtown Montreal
29          H4G                                     Verdun, Quebec
30          H7G                                  Pont-Viau, Quebec
31          H9G                                Dollard-des-Ormeaux
32          H1H                                      Montréal-Nord
33          H2H                                        The Plateau
34          H3H                                  Downtown Montreal
35          H4H                                     Verdun, Quebec
36          H7H                                    Auteuil, Quebec
37          H9H                           Sainte-Geneviève, Quebec
38          H1J                                      Anjou, Quebec
39          H2J                                        The Plateau
40          H3J                                   Petite-Bourgogne
41          H4J                               Cartierville, Quebec
42          H7J                                    Auteuil, Quebec
43          H9J                                   Kirkland, Quebec
44          H1K                                      Anjou, Quebec
45          H2K                                 Centre-Sud, Quebec
46          H3K                       Pointe-Saint-Charles, Quebec
47          H4K                               Cartierville, Quebec
48          H7K                                    Auteuil, Quebec
49          H9K                                 Senneville, Quebec
50          H1L                                 Mercier (Montreal)
51          H2L                                 Centre-Sud, Quebec
52          H3L                                   Ahuntsic, Quebec
53          H4L                              Saint-Laurent, Quebec
54          H7L                                Sainte-Rose, Quebec
55          H1M                                 Mercier (Montreal)
56          H2M                                   Ahuntsic, Quebec
57          H3M                               Cartierville, Quebec
58          H4M                              Saint-

To find the longitude and latitude in terms of the Neighborhoods. I'm going to change the names of 2 of the neighborhoods that wasn't able to find the coordinates.

In [24]:
df["Neighborhoods"].replace({"Saint-Michel district, Quebec": "Saint-Michel, Montreal", "Ville Saint-Pierre, Quebec": "Saint-Pierre, Montreal",
                            "The Plateau":"The Plateau,Montreal","Centre-Sud, Quebec":'Centre-sud, Montreal,Canada'
}, inplace=True)

We can now work with the data

### Find Longitude and Latitude of Every Neighborhood

In [25]:
#!pip install geocoder
#!pip install geopy

The Nominatim API will be used to find the different coordinates of the cities. 

In [26]:
from geopy.geocoders import Nominatim

def get_geocoder(city):
    geolocator = Nominatim(user_agent="#EMAIL HERE#",country_bias='ca')
    location = geolocator.geocode('{}'.format(city))
    print(city)
    if not location:
        return 'none','none'

    return location.latitude, location.longitude

In [30]:
df['Latitude'], df['Longitude'] = zip(*df['Neighborhoods'].apply(get_geocoder))

C:\Users\mecqu\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: DeprecationWarning: `country_bias` argument of the Nominatim.__init__ is deprecated and will be removed in geopy 2.0. Use Nominatim.geocode(country_codes='ca') instead.
  after removing the cwd from sys.path.


Pointe-aux-Trembles
Saint-Michel, Montreal
Downtown Montreal
Notre-Dame-de-Grâce, Quebec
Place Bonaventure
Duvernay-Est, Quebec
Dollard-des-Ormeaux
Montreal East, Quebec
Ahuntsic, Quebec
Downtown Montreal
Notre-Dame-de-Grâce, Quebec
Place Desjardins
Saint-François, Laval, Quebec
Dollard-des-Ormeaux
Rivière-des-Prairies
Ahuntsic, Quebec
Griffintown, Quebec
Saint-Henri, Montreal
Saint-Vincent-de-Paul, Quebec
L'Île-Bizard, Quebec
Rivière-des-Prairies
Villeray, Quebec
L'Île-Des-Soeurs, Quebec
Ville Émard, Quebec
Duvernay, Quebec
L'Île-Bizard, Quebec
Montréal-Nord
Petite-Patrie, Quebec
Downtown Montreal
Verdun, Quebec
Pont-Viau, Quebec
Dollard-des-Ormeaux
Montréal-Nord
The Plateau,Montreal
Downtown Montreal
Verdun, Quebec
Auteuil, Quebec
Sainte-Geneviève, Quebec
Anjou, Quebec
The Plateau,Montreal
Petite-Bourgogne
Cartierville, Quebec
Auteuil, Quebec
Kirkland, Quebec
Anjou, Quebec
Centre-sud, Montreal,Canada
Pointe-Saint-Charles, Quebec
Cartierville, Quebec
Auteuil, Quebec
Senneville, Quebec

In [31]:
df

Postal Code                                      Neighborhoods   Latitude  \
0           H1A                                Pointe-aux-Trembles  45.667824   
1           H2A                             Saint-Michel, Montreal  45.568702   
2           H3A                                  Downtown Montreal  45.505290   
3           H4A                        Notre-Dame-de-Grâce, Quebec  45.467967   
4           H5A                                  Place Bonaventure  45.499583   
5           H7A                               Duvernay-Est, Quebec  45.593140   
6           H9A                                Dollard-des-Ormeaux  45.484230   
7           H1B                              Montreal East, Quebec  45.497216   
8           H2B                                   Ahuntsic, Quebec  45.559308   
9           H3B                                  Downtown Montreal  45.505290   
10          H4B                        Notre-Dame-de-Grâce, Quebec  45.467967   
11          H5B                                   Place Desjardins  45.507424   
12          H7B                      Saint-François, Laval, Quebec  45.663905   
13          H9B                                Dollard-des-Ormeaux  45.484230   
14          H1C                               Rivière-des-Prairies  45.667964   
15          H2C                                   Ahuntsic, Quebec  45.559308   
16          H3C                                Griffintown, Quebec  45.489897   
17          H4C                              Saint-Henri, Montreal  45.478460   
18          H7C                      Saint-Vincent-de-Paul, Quebec  45.614695   
19          H9C                               L'Île-Bizard, Quebec  45.495042   
20          H1E                               Rivière-des-Prairies  45.667964   
21          H2E                                   Villeray, Quebec  45.558557   
22          H3E                           L'Île-Des-Soeurs, Quebec  45.460363   
23          H4E                                Ville Émard, Quebec  45.455756   
24          H7E                                   Duvernay, Quebec  45.593550   
25          H9E                               L'Île-Bizard, Quebec  45.495042   
26          H1G                                      Montréal-Nord  45.593899   
27          H2G                              Petite-Patrie, Quebec  45.550747   
28          H3G                                  Downtown Montreal  45.505290   
29          H4G                                     Verdun, Quebec  45.459078   
30          H7G                                  Pont-Viau, Quebec  45.557253   
31          H9G                                Dollard-des-Ormeaux  45.484230   
32          H1H                                      Montréal-Nord  45.593899   
33          H2H                               The Plateau,Montreal  45.525370   
34          H3H                                  Downtown Montreal  45.505290   
35          H4H                                     Verdun, Quebec  45.459078   
36          H7H                                    Auteuil, Quebec  45.631013   
37          H9H                           Sainte-Geneviève, Quebec  45.480472   
38          H1J                                      Anjou, Quebec  45.604898   
39          H2J                               The Plateau,Montreal  45.525370   
40          H3J                                   Petite-Bourgogne  45.488366   
41          H4J                               Cartierville, Quebec  45.522935   
42          H7J                                    Auteuil, Quebec  45.631013   
43          H9J                                   Kirkland, Quebec  45.452919   
44          H1K                                      Anjou, Quebec  45.604898   
45          H2K                        Centre-sud, Montreal,Canada  45.573143   
46          H3K                       Pointe-Saint-Charles, Quebec  45.480093   
47          H4K                               Cartierville, Quebec  45.522935   
48          H7K                    

In [32]:
#Check to see if coordinates were not found according to the postal code
df.loc[df['Latitude'] == 'none']

C:\Users\mecqu\Anaconda3\lib\site-packages\pandas\core\ops\array_ops.py:253: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  res_values = method(rvalues)


Empty DataFrame
Columns: [Postal Code, Neighborhoods, Latitude, Longitude]
Index: []

### Import Foursquare Credentials

In [33]:
CLIENT_ID = '' # your Foursquare ID
CLIENT_SECRET = '' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentials:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentials:
CLIENT_ID: TY4WO12LKG12BQRG00PK44BKO24YCMVGJUMP1XY33TYPV22J
CLIENT_SECRET:NXVHKY3RYLM1TUSB2252CLADWJIJOVOQ5GDQVYQQRXTZF2L0


In [34]:
# create map of Montreal using latitude and longitude values
map_MTL = folium.Map(location=[45.5017, -73.5673], zoom_start=10)

# add markers to map
for lat, lng, neighborhood in zip(df['Latitude'], df['Longitude'],  df['Neighborhoods']):
    label = '{}, '.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_MTL)  
    
map_MTL

Initially looking at the map, there was multiple points that are out of Montreal. I manually changed them manually with previous code. I notice using Nominatim's API give out of location. Unfortunately, using Postal Codes did not work with it ( Canadian Postal Codes ) The neighborgoods were used instead.

In [35]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [36]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
             100)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhoods', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [37]:
MTL_venues = getNearbyVenues(names=df['Neighborhoods'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )


Pointe-aux-Trembles
Saint-Michel, Montreal
Downtown Montreal
Notre-Dame-de-Grâce, Quebec
Place Bonaventure
Duvernay-Est, Quebec
Dollard-des-Ormeaux
Montreal East, Quebec
Ahuntsic, Quebec
Downtown Montreal
Notre-Dame-de-Grâce, Quebec
Place Desjardins
Saint-François, Laval, Quebec
Dollard-des-Ormeaux
Rivière-des-Prairies
Ahuntsic, Quebec
Griffintown, Quebec
Saint-Henri, Montreal
Saint-Vincent-de-Paul, Quebec
L'Île-Bizard, Quebec
Rivière-des-Prairies
Villeray, Quebec
L'Île-Des-Soeurs, Quebec
Ville Émard, Quebec
Duvernay, Quebec
L'Île-Bizard, Quebec
Montréal-Nord
Petite-Patrie, Quebec
Downtown Montreal
Verdun, Quebec
Pont-Viau, Quebec
Dollard-des-Ormeaux
Montréal-Nord
The Plateau,Montreal
Downtown Montreal
Verdun, Quebec
Auteuil, Quebec
Sainte-Geneviève, Quebec
Anjou, Quebec
The Plateau,Montreal
Petite-Bourgogne
Cartierville, Quebec
Auteuil, Quebec
Kirkland, Quebec
Anjou, Quebec
Centre-sud, Montreal,Canada
Pointe-Saint-Charles, Quebec
Cartierville, Quebec
Auteuil, Quebec
Senneville, Quebec

In [38]:
print(MTL_venues.shape)


(1993, 7)


In [39]:
MTL_venues

Neighborhoods  \
0                                   Pointe-aux-Trembles   
1                                   Pointe-aux-Trembles   
2                                   Pointe-aux-Trembles   
3                                   Pointe-aux-Trembles   
4                                Saint-Michel, Montreal   
5                                Saint-Michel, Montreal   
6                                Saint-Michel, Montreal   
7                                Saint-Michel, Montreal   
8                                     Downtown Montreal   
9                                     Downtown Montreal   
10                                    Downtown Montreal   
11                                    Downtown Montreal   
12                                    Downtown Montreal   
13                                    Downtown Montreal   
14                                    Downtown Montreal   
15                                    Downtown Montreal   
16                                    Downtown Montreal   
17                                    Downtown Montreal   
18                                    Downtown Montreal   
19                                    Downtown Montreal   
20                                    Downtown Montreal   
21                                    Downtown Montreal   
22                                    Downtown Montreal   
23                                    Downtown Montreal   
24                                    Downtown Montreal   
25                                    Downtown Montreal   
26                                    Downtown Montreal   
27                                    Downtown Montreal   
28                                    Downtown Montreal   
29                                    Downtown Montreal   
30                                    Downtown Montreal   
31                                    Downtown Montreal   
32                                    Downtown Montreal   
33                                    Downtown Montreal   
34                                    Downtown Montreal   
35                                    Downtown Montreal   
36                                    Downtown Montreal   
37                                    Downtown Montreal   
38                                    Downtown Montreal   
39                                    Downtown Montreal   
40                                    Downtown Montreal   
41                                    Downtown Montreal   
42                                    Downtown Montreal   
43                                    Downtown Montreal   
44                                    Downtown Montreal   
45                                    Downtown Montreal   
46                                    Downtown Montreal   
47                                    Downtown Montreal   
48                                    Downtown Montreal   
49                                    Downtown Montreal   
50                                    Downtown Montreal   
51                                    Downtown Montreal   
52                                    Downtown Montreal   
53                                    Downtown Montreal   
54                                    Downtown Montreal   
55                                    Downtown Montreal   
56                                    Downtown Montreal   
57                                    Downtown Montreal   
58                                    Downtown Montreal   
59                                    Downtown Montreal   
60                                    Downtown Montreal   
61                                    Downtown Montreal   
62                                    Downtown Montreal   
63                                    Downtown Montreal   
64                                    Downtown Montreal   
65                                    Downtown Montreal   
66                                    Downtown Montreal   
67                            

In [196]:
MTL_venues.groupby('Neighborhoods').count().head()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhoods                                                                
Ahuntsic, Quebec                         75                      75     75   
Anjou, Quebec                             4                       4      4   
Auteuil, Quebec                          15                      15     15   
Beaconsfield, Quebec                      5                       5      5   
Cartierville, Quebec                      6                       6      6   

                      Venue Latitude  Venue Longitude  Venue Category  
Neighborhoods                                                          
Ahuntsic, Quebec                  75               75              75  
Anjou, Quebec                      4                4               4  
Auteuil, Quebec                   15               15              15  
Beaconsfield, Quebec               5                5               5  
Cartierville, Quebec               6                6               6

In [41]:
print('There are {} uniques categories.'.format(len(MTL_venues['Venue Category'].unique())))

There are 195 uniques categories.


### Analyzing Each Neighbohood

In [42]:
# one hot encoding
MTL_onehot = pd.get_dummies(MTL_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
MTL_onehot['Neighborhoods'] = MTL_venues['Neighborhoods'] 

# move neighborhood column to the first column
fixed_columns = [MTL_onehot.columns[-1]] + list(MTL_onehot.columns[:-1])
MTL_onehot = MTL_onehot[fixed_columns]

MTL_onehot.head()

Neighborhoods  Adult Boutique  Airport Service  \
0     Pointe-aux-Trembles               0                0   
1     Pointe-aux-Trembles               0                0   
2     Pointe-aux-Trembles               0                0   
3     Pointe-aux-Trembles               0                0   
4  Saint-Michel, Montreal               0                0   

   American Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                    0            0           0                    0   
1                    0            0           0                    0   
2                    0            0           0                    0   
3                    0            0           0                    0   
4                    0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Automotive Shop  BBQ Joint  Bakery  \
0                 0                   0                0          0       0   
1                 0                   0                0          0       0   
2                 0                   0                0          0       0   
3                 0                   0                0          0       0   
4                 0                   0                0          0       0   

   Bank  Bar  Basketball Court  Beer Store  Big Box Store  \
0     0    0                 0           0              0   
1     0    0                 0           0              0   
2     0    0                 0           0              0   
3     0    0                 0           0              0   
4     0    0                 0           0              0   

   Bike Rental / Bike Share  Bistro  Boat or Ferry  Bookstore  Boutique  \
0                         0       0              0          0         0   
1                         0       0              0          0         0   
2                         0       0              0          0         0   
3                         0       0              0          0         0   
4                         0       0              0          0         0   

   Boxing Gym  Breakfast Spot  Brewery  Bubble Tea Shop  Building  \
0           0               0        0                0         0   
1           0               0        0                0         0   
2           0               0        0                0         0   
3           0               0        0                0         0   
4           0               0        0                0         0   

   Burger Joint  Bus Line  Bus Station  Bus Stop  Business Service  Butcher  \
0             0         0            0         0                 0        0   
1             0         0            0         0                 0        0   
2             0         0            0         0                 0        0   
3             0         0            0         0                 0        0   
4             0         0            0         0                 0        0   

   Café  Cambodian Restaurant  Caribbean Restaurant  Cheese Shop  \
0     0                     0                     0            0   
1     0                     0                     0            0   
2     0                     0                     0            0   
3     0                     0                     0            0   
4     0                     0                     0            0   

   Chinese Restaurant  Chocolate Shop  Church  Climbing Gym  Clothing Store  \
0                   0               0       0             0               0   
1                   0               0       0             0               0   
2                   0               0       0             0               0   
3                   0               0       0             0               0   
4                   0               0       0             0               0   

   Cocktail Bar  Coffee Shop  Comedy Club  Comfort Food Restaurant  \
0             0            0            0                        0   

In [43]:
MTL_onehot.shape

(1993, 196)

In [44]:
MTL_grouped = MTL_onehot.groupby('Neighborhoods').mean().reset_index()
MTL_grouped

Neighborhoods  Adult Boutique  \
0                                    Ahuntsic, Quebec        0.000000   
1                                       Anjou, Quebec        0.000000   
2                                     Auteuil, Quebec        0.000000   
3                                Beaconsfield, Quebec        0.000000   
4                                Cartierville, Quebec        0.000000   
5                         Centre-sud, Montreal,Canada        0.000000   
6                                    Chomedey, Quebec        0.000000   
7                                      Côte Saint-Luc        0.000000   
8                             Côte-des-Neiges, Quebec        0.000000   
9                                 Dollard-des-Ormeaux        0.000000   
10                                             Dorval        0.000000   
11                                     Dorval, Quebec        0.000000   
12                                  Downtown Montreal        0.000000   
13                                   Duvernay, Quebec        0.000000   
14                               Duvernay-Est, Quebec        0.000000   
15                                Griffintown, Quebec        0.000000   
16                                  Hampstead, Quebec        0.000000   
17                                  Hochelaga, Quebec        0.000000   
18                                   Kirkland, Quebec        0.000000   
19                               L'Île-Bizard, Quebec        0.000000   
20                           L'Île-Des-Soeurs, Quebec        0.000000   
21                               L'Île-Dorval, Quebec        0.000000   
22                                    LaSalle, Quebec        0.000000   
23                                    Lachine, Quebec        0.000000   
24                                  Laval-des-Rapides        0.000000   
25                                   Laval-sur-le-Lac        0.000000   
26                                Maisonneuve, Quebec        0.000000   
27                              Montreal East, Quebec        0.000000   
28                              Montreal West, Quebec        0.000000   
29                                      Montréal-Nord        0.000000   
30  Montréal-Pierre Elliott Trudeau International ...        0.000000   
31                                Mount Royal, Quebec        0.000000   
32                        Notre-Dame-de-Grâce, Quebec        0.000000   
33                                       Old Montreal        0.000000   
34                                  Outremont, Quebec        0.000000   
35                             Parc-Extension, Quebec        0.000000   
36                                   Petite-Bourgogne        0.000000   
37                              Petite-Patrie, Quebec        0.000000   
38                                Pierrefonds-Roxboro        0.000000   
39                                  Place Bonaventure        0.000000   
40                                   Place Desjardins        0.000000   
41                                      Pointe-Claire        0.000000   
42                       Pointe-Saint-Charles, Quebec        0.000000   
43                                Pointe-aux-Trembles        0.000000   
44                                  Pont-Viau, Quebec        0.333333   
45                               Rivière-des-Prairies        0.000000   
46                                   Rosemont, Quebec        0.000000   
47                      Saint-François, Laval, Quebec        0.000000   
48                              Saint-Henri, Montreal        0.000000   
49                              Saint-Laurent, Quebec        0.000000   
50                              Saint-Léonard, Quebec        0.000000   
51                             Saint-Michel, Montreal        0.000000   
52                             Saint-Pierre, Montreal        0.000000   
53                      Saint-Vincent-de-Paul, Quebec        0.000000   
54                    Sai

### Let's look at the top 5 common venues

In [45]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [46]:
num_top_venues = 5

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhoods']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhoods'] = MTL_grouped['Neighborhoods']

for ind in np.arange(MTL_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(MTL_grouped.iloc[ind, :], num_top_venues)



In [47]:
neighborhoods_venues_sorted

Neighborhoods  \
0                                    Ahuntsic, Quebec   
1                                       Anjou, Quebec   
2                                     Auteuil, Quebec   
3                                Beaconsfield, Quebec   
4                                Cartierville, Quebec   
5                         Centre-sud, Montreal,Canada   
6                                    Chomedey, Quebec   
7                                      Côte Saint-Luc   
8                             Côte-des-Neiges, Quebec   
9                                 Dollard-des-Ormeaux   
10                                             Dorval   
11                                     Dorval, Quebec   
12                                  Downtown Montreal   
13                                   Duvernay, Quebec   
14                               Duvernay-Est, Quebec   
15                                Griffintown, Quebec   
16                                  Hampstead, Quebec   
17                                  Hochelaga, Quebec   
18                                   Kirkland, Quebec   
19                               L'Île-Bizard, Quebec   
20                           L'Île-Des-Soeurs, Quebec   
21                               L'Île-Dorval, Quebec   
22                                    LaSalle, Quebec   
23                                    Lachine, Quebec   
24                                  Laval-des-Rapides   
25                                   Laval-sur-le-Lac   
26                                Maisonneuve, Quebec   
27                              Montreal East, Quebec   
28                              Montreal West, Quebec   
29                                      Montréal-Nord   
30  Montréal-Pierre Elliott Trudeau International ...   
31                                Mount Royal, Quebec   
32                        Notre-Dame-de-Grâce, Quebec   
33                                       Old Montreal   
34                                  Outremont, Quebec   
35                             Parc-Extension, Quebec   
36                                   Petite-Bourgogne   
37                              Petite-Patrie, Quebec   
38                                Pierrefonds-Roxboro   
39                                  Place Bonaventure   
40                                   Place Desjardins   
41                                      Pointe-Claire   
42                       Pointe-Saint-Charles, Quebec   
43                                Pointe-aux-Trembles   
44                                  Pont-Viau, Quebec   
45                               Rivière-des-Prairies   
46                                   Rosemont, Quebec   
47                      Saint-François, Laval, Quebec   
48                              Saint-Henri, Montreal   
49                              Saint-Laurent, Quebec   
50                              Saint-Léonard, Quebec   
51                             Saint-Michel, Montreal   
52                             Saint-Pierre, Montreal   
53                      Saint-Vincent-de-Paul, Quebec   
54                    Sainte-Anne-de-Bellevue, Quebec   
55                            Sainte-Dorothée, Quebec   
56                           Sainte-Geneviève, Quebec   
57                                Sainte-Rose, Quebec   
58                                 Senneville, Quebec   
59                               The Plateau,Montreal   
60                                  Tour de la Bourse   
61                                     Verdun, Quebec   
62                                Ville Émard, Quebec   
63                                   Villeray, Quebec   
64                                     Vimont, Quebec   
65                                  Westmount, Quebec   
66                                         Îles-Laval   

         1st Most Common Venue      2nd Most Common Venue  \
0                   Restaurant                       Café   
1        Portuguese Restaurant           

### Clutering Neighborhoods

In [48]:
# set number of clusters
kclusters = 5

MTL_grouped_clustering = MTL_grouped.drop('Neighborhoods', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(MTL_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:5] 

array([4, 4, 1, 4, 0])

In [195]:
# add clustering labels
#neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

MTL_merged = df

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
MTL_merged = MTL_merged.join(neighborhoods_venues_sorted.set_index('Neighborhoods'), on='Neighborhoods')

MTL_merged.head() # check the last columns!

Postal Code                Neighborhoods   Latitude  Longitude  \
0         H1A          Pointe-aux-Trembles  45.667824 -73.505133   
1         H2A       Saint-Michel, Montreal  45.568702 -73.621495   
2         H3A            Downtown Montreal  45.505290 -73.564076   
3         H4A  Notre-Dame-de-Grâce, Quebec  45.467967 -73.628922   
4         H5A            Place Bonaventure  45.499583 -73.564917   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0             1.0     Convenience Store              Pharmacy   
1             1.0     Convenience Store              Pharmacy   
2             4.0                  Café                 Hotel   
3             4.0                  Café         Grocery Store   
4             4.0            Restaurant                  Café   

  3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  
0           Supermarket       Sushi Restaurant              Dive Bar  
1      Department Store                   Park              Dive Bar  
2                 Plaza      French Restaurant            Restaurant  
3                  Park            Pizza Place        Sandwich Place  
4                 Plaza  Portuguese Restaurant           Coffee Shop

In [50]:
MTL_merged.dropna(inplace=True)
convert_dict = {'Cluster Labels':int}
MTL_merged=MTL_merged.astype(convert_dict)



In [51]:
# create map
map_clusters = folium.Map(location=[45.5017, -73.5673], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(MTL_merged['Latitude'], MTL_merged['Longitude'], MTL_merged['Neighborhoods'], MTL_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### Analyzing the clusters

Let's analyze the cluster looking and look at their 5 most common Venues

In [52]:
MTL_merged.loc[MTL_merged['Cluster Labels'] == 0, MTL_merged.columns[[1] + list(range(5, MTL_merged.shape[1]))]]

Neighborhoods 1st Most Common Venue 2nd Most Common Venue  \
22      L'Île-Des-Soeurs, Quebec                  Park     Convenience Store   
30             Pont-Viau, Quebec        Adult Boutique           Coffee Shop   
41          Cartierville, Quebec          Empada House                  Park   
45   Centre-sud, Montreal,Canada                  Park           Golf Course   
47          Cartierville, Quebec          Empada House                  Park   
51   Centre-sud, Montreal,Canada                  Park           Golf Course   
54           Sainte-Rose, Quebec          Skating Rink         Train Station   
57          Cartierville, Quebec          Empada House                  Park   
106            Hampstead, Quebec                  Park         Big Box Store   

        3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
22   Mediterranean Restaurant              Dive Bar  Fast Food Restaurant  
30                       Park              Dive Bar  Fast Food Restaurant  
41                Yoga Studio              Dive Bar  Fast Food Restaurant  
45                 Food Truck           Yoga Studio        Farmers Market  
47                Yoga Studio              Dive Bar  Fast Food Restaurant  
51                 Food Truck           Yoga Studio        Farmers Market  
54                       Park           Yoga Studio              Dive Bar  
57                Yoga Studio              Dive Bar  Fast Food Restaurant  
106               Yoga Studio               Dog Run   Filipino Restaurant

In [53]:
MTL_merged.loc[MTL_merged['Cluster Labels'] == 1, MTL_merged.columns[[1] + list(range(5, MTL_merged.shape[1]))]]

Neighborhoods 1st Most Common Venue 2nd Most Common Venue  \
0       Pointe-aux-Trembles     Convenience Store              Pharmacy   
1    Saint-Michel, Montreal     Convenience Store              Pharmacy   
23      Ville Émard, Quebec         Grocery Store                  Park   
27    Petite-Patrie, Quebec         Grocery Store              Pharmacy   
36          Auteuil, Quebec     Convenience Store        Farmers Market   
42          Auteuil, Quebec     Convenience Store        Farmers Market   
48          Auteuil, Quebec     Convenience Store        Farmers Market   
81    Petite-Patrie, Quebec         Grocery Store              Pharmacy   
115              Îles-Laval              Pharmacy              Platform   
117  Saint-Michel, Montreal     Convenience Store              Pharmacy   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
0             Supermarket      Sushi Restaurant              Dive Bar  
1        Department Store                  Park              Dive Bar  
23      Convenience Store        Sandwich Place              Pharmacy  
27         Shopping Plaza        Ice Cream Shop        Sandwich Place  
36               Pharmacy           Coffee Shop         Grocery Store  
42               Pharmacy           Coffee Shop         Grocery Store  
48               Pharmacy           Coffee Shop         Grocery Store  
81         Shopping Plaza        Ice Cream Shop        Sandwich Place  
115                   Gym        Sandwich Place        Discount Store  
117      Department Store                  Park              Dive Bar

In [54]:
MTL_merged.loc[MTL_merged['Cluster Labels'] == 2, MTL_merged.columns[[1] + list(range(5, MTL_merged.shape[1]))]]

Neighborhoods 1st Most Common Venue  \
114  Montréal-Pierre Elliott Trudeau International ...       Airport Service   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
114           Yoga Studio              Dive Bar   Filipino Restaurant   

    5th Most Common Venue  
114  Fast Food Restaurant

In [55]:
MTL_merged.loc[MTL_merged['Cluster Labels'] == 3, MTL_merged.columns[[1] + list(range(5, MTL_merged.shape[1]))]]

Neighborhoods 1st Most Common Venue 2nd Most Common Venue  \
86  L'Île-Dorval, Quebec         Boat or Ferry           Yoga Studio   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  
86               Dog Run   Filipino Restaurant  Fast Food Restaurant

In [192]:
MTL_merged.loc[MTL_merged['Cluster Labels'] == 4, MTL_merged.columns[[1] + list(range(5, MTL_merged.shape[1]))]].head()

Neighborhoods 1st Most Common Venue 2nd Most Common Venue  \
2            Downtown Montreal                  Café                 Hotel   
3  Notre-Dame-de-Grâce, Quebec                  Café         Grocery Store   
4            Place Bonaventure            Restaurant                  Café   
5         Duvernay-Est, Quebec                  Bank              Pharmacy   
6          Dollard-des-Ormeaux    Italian Restaurant          Skating Rink   

  3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  
2                 Plaza      French Restaurant            Restaurant  
3                  Park            Pizza Place        Sandwich Place  
4                 Plaza  Portuguese Restaurant           Coffee Shop  
5           Coffee Shop          Shopping Mall        Sandwich Place  
6  Fast Food Restaurant       Greek Restaurant     Food & Drink Shop

### Analysis of the 4 Labels

Analyzing the four labels we can see that the 1st label mostly represents the neighborhoods where the restauration sector is prominent. Let us look into it more closesly.

In [201]:
#Convert MTL_merged to string to anylyze
MTL_merged[['1st Most Common Venue',
            '2nd Most Common Venue',
            '3rd Most Common Venue',
            '4th Most Common Venue',
            '5th Most Common Venue']] = MTL_merged[['1st Most Common Venue',
                                                    '2nd Most Common Venue',
                                                    '3rd Most Common Venue',
                                                    '4th Most Common Venue',
                                                    '5th Most Common Venue']].astype("string")


Let us create a data frame with the 4th cluster and let's look at the ones with Retaurant as it's 1st most common venue

In [202]:
MTL_4 = MTL_merged.loc[MTL_merged['Cluster Labels'] == 4 , MTL_merged.columns[[1] + list(range(5, MTL_merged.shape[1]))]]
MTL_Restaurants=MTL_4.loc[MTL_merged["1st Most Common Venue"].str.contains( 'Restaurant')]

MTL_Restaurants

ValueError: cannot mask with array containing NA / NaN values

The cities above would be recommended places that would give clients and excellent culinary experience. However, what if we dive deeper and see which one has the most restaurants in their given location.

#### Quantity of Restaurants per Location

The next step would be to look at the number of restaurant each venue has. With this, we can now determine "quantity" wise where would be the best culinary experience to have in Montreal.

In [134]:
s1 = pd.merge(MTL_venues, MTL_Restaurants, how='inner', on=['Neighborhoods'])

In [135]:
s1

Neighborhoods  Neighborhood Latitude  Neighborhood Longitude  \
0            Place Bonaventure              45.499583              -73.564917   
1            Place Bonaventure              45.499583              -73.564917   
2            Place Bonaventure              45.499583              -73.564917   
3            Place Bonaventure              45.499583              -73.564917   
4            Place Bonaventure              45.499583              -73.564917   
5            Place Bonaventure              45.499583              -73.564917   
6            Place Bonaventure              45.499583              -73.564917   
7            Place Bonaventure              45.499583              -73.564917   
8            Place Bonaventure              45.499583              -73.564917   
9            Place Bonaventure              45.499583              -73.564917   
10           Place Bonaventure              45.499583              -73.564917   
11           Place Bonaventure              45.499583              -73.564917   
12           Place Bonaventure              45.499583              -73.564917   
13           Place Bonaventure              45.499583              -73.564917   
14           Place Bonaventure              45.499583              -73.564917   
15           Place Bonaventure              45.499583              -73.564917   
16           Place Bonaventure              45.499583              -73.564917   
17           Place Bonaventure              45.499583              -73.564917   
18           Place Bonaventure              45.499583              -73.564917   
19           Place Bonaventure              45.499583              -73.564917   
20           Place Bonaventure              45.499583              -73.564917   
21           Place Bonaventure              45.499583              -73.564917   
22           Place Bonaventure              45.499583              -73.564917   
23           Place Bonaventure              45.499583              -73.564917   
24           Place Bonaventure              45.499583              -73.564917   
25           Place Bonaventure              45.499583              -73.564917   
26           Place Bonaventure              45.499583              -73.564917   
27           Place Bonaventure              45.499583              -73.564917   
28           Place Bonaventure              45.499583              -73.564917   
29           Place Bonaventure              45.499583              -73.564917   
30           Place Bonaventure              45.499583              -73.564917   
31           Place Bonaventure              45.499583              -73.564917   
32         Dollard-des-Ormeaux              45.484230              -73.806455   
33         Dollard-des-Ormeaux              45.484230              -73.806455   
34         Dollard-des-Ormeaux              45.484230              -73.806455   
35         Dollard-des-Ormeaux              45.484230              -73.806455   
36         Dollard-des-Ormeaux              45.484230              -73.806455   
37         Dollard-des-Ormeaux              45.484230              -73.806455   
38         Dollard-des-Ormeaux              45.484230              -73.806455   
39         Dollard-des-Ormeaux              45.484230              -73.806455   
40         Dollard-des-Ormeaux              45.484230              -73.806455   
41         Dollard-des-Ormeaux              45.484230              -73.806455   
42         Dollard-des-Ormeaux              45.484230              -73.806455   
43         Dollard-des-Ormeaux              45.484230              -73.806455   
44         Dollard-des-Ormeaux              45.484230              -73.806455   
45         Dollard-des-Ormeaux              45.484230              -73.806455   
46         Dollard-des-Ormeaux              45.484230              -73.806455   
47         Dollard-des-Ormeaux              45.484230              -73.806455   
48         Dollard-des-Ormeaux              45.4

In [136]:
s1=s1[["Neighborhoods","Neighborhood Latitude","Neighborhood Longitude","Venue","Venue Category"]]

In [137]:
s1


Neighborhoods  Neighborhood Latitude  Neighborhood Longitude  \
0            Place Bonaventure              45.499583              -73.564917   
1            Place Bonaventure              45.499583              -73.564917   
2            Place Bonaventure              45.499583              -73.564917   
3            Place Bonaventure              45.499583              -73.564917   
4            Place Bonaventure              45.499583              -73.564917   
5            Place Bonaventure              45.499583              -73.564917   
6            Place Bonaventure              45.499583              -73.564917   
7            Place Bonaventure              45.499583              -73.564917   
8            Place Bonaventure              45.499583              -73.564917   
9            Place Bonaventure              45.499583              -73.564917   
10           Place Bonaventure              45.499583              -73.564917   
11           Place Bonaventure              45.499583              -73.564917   
12           Place Bonaventure              45.499583              -73.564917   
13           Place Bonaventure              45.499583              -73.564917   
14           Place Bonaventure              45.499583              -73.564917   
15           Place Bonaventure              45.499583              -73.564917   
16           Place Bonaventure              45.499583              -73.564917   
17           Place Bonaventure              45.499583              -73.564917   
18           Place Bonaventure              45.499583              -73.564917   
19           Place Bonaventure              45.499583              -73.564917   
20           Place Bonaventure              45.499583              -73.564917   
21           Place Bonaventure              45.499583              -73.564917   
22           Place Bonaventure              45.499583              -73.564917   
23           Place Bonaventure              45.499583              -73.564917   
24           Place Bonaventure              45.499583              -73.564917   
25           Place Bonaventure              45.499583              -73.564917   
26           Place Bonaventure              45.499583              -73.564917   
27           Place Bonaventure              45.499583              -73.564917   
28           Place Bonaventure              45.499583              -73.564917   
29           Place Bonaventure              45.499583              -73.564917   
30           Place Bonaventure              45.499583              -73.564917   
31           Place Bonaventure              45.499583              -73.564917   
32         Dollard-des-Ormeaux              45.484230              -73.806455   
33         Dollard-des-Ormeaux              45.484230              -73.806455   
34         Dollard-des-Ormeaux              45.484230              -73.806455   
35         Dollard-des-Ormeaux              45.484230              -73.806455   
36         Dollard-des-Ormeaux              45.484230              -73.806455   
37         Dollard-des-Ormeaux              45.484230              -73.806455   
38         Dollard-des-Ormeaux              45.484230              -73.806455   
39         Dollard-des-Ormeaux              45.484230              -73.806455   
40         Dollard-des-Ormeaux              45.484230              -73.806455   
41         Dollard-des-Ormeaux              45.484230              -73.806455   
42         Dollard-des-Ormeaux              45.484230              -73.806455   
43         Dollard-des-Ormeaux              45.484230              -73.806455   
44         Dollard-des-Ormeaux              45.484230              -73.806455   
45         Dollard-des-Ormeaux              45.484230              -73.806455   
46         Dollard-des-Ormeaux              45.484230              -73.806455   
47         Dollard-des-Ormeaux              45.484230              -73.806455   
48         Dollard-des-Ormeaux              45.4

Removing all the "Fast Food Restaurants" and the duplicates in this Dataframe

In [138]:
#Removing Fast Food Restaurant
fastfood = s1[s1['Venue Category'] == 'Fast Food Restaurant'].index
s1.drop(fastfood, inplace = True)

C:\Users\mecqu\Anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [140]:
#Removing the Duplicates
s1.drop_duplicates(subset = "Venue",keep = 'first', inplace = True)

C:\Users\mecqu\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [169]:
s1.head()

Neighborhoods  Neighborhood Latitude  Neighborhood Longitude  \
0  Place Bonaventure              45.499583              -73.564917   
1  Place Bonaventure              45.499583              -73.564917   
2  Place Bonaventure              45.499583              -73.564917   
3  Place Bonaventure              45.499583              -73.564917   
4  Place Bonaventure              45.499583              -73.564917   

                             Venue         Venue Category  
0                        96,9 CKOI            Music Venue  
1                        Portus360  Portuguese Restaurant  
2                          Nacarat           Cocktail Bar  
3  Cathédrale Marie-Reine-du-Monde                 Church  
4                 Première Moisson                 Bakery

In [172]:
s1[['Venue Category','Neighborhoods']].groupby('Neighborhoods').count()


Venue Category
Neighborhoods                           
Ahuntsic, Quebec                      14
Anjou, Quebec                          2
Chomedey, Quebec                      10
Dollard-des-Ormeaux                   17
Griffintown, Quebec                   32
Kirkland, Quebec                       7
LaSalle, Quebec                       19
Old Montreal                          75
Parc-Extension, Quebec                 8
Petite-Bourgogne                       8
Place Bonaventure                     32
Place Desjardins                      89
Saint-Pierre, Montreal                 4
Sainte-Geneviève, Quebec               4
Senneville, Quebec                     1
The Plateau,Montreal                  17

Let's clean this up and only take venues that are actually restaurants. 

In [197]:
searchfor=['Restaurant','Breakfast','Coffee Shop','Steakhouse','Food Truck','Taco Place','Burger Joint','Breakfast', 'Bar', 'Deli','Bakery',
          'BBQ','Food','Sandwich','Fish','Dessert','Bistro','Gastropub','Bar','Diner','Café','Tea','Bakery', 'Pizza']
s2=s1[s1["Venue Category"].str.contains('|'.join(searchfor) )].groupby('Neighborhoods').count()
foodieplaces=pd.DataFrame()
foodieplaces['Number of Restaurants'] = s2['Venue Category']
foodieplaces.sort_values(by = 'Number of Restaurants', ascending = False)

Number of Restaurants
Neighborhoods                                  
Place Desjardins                             55
Old Montreal                                 45
Place Bonaventure                            20
Griffintown, Quebec                          19
Dollard-des-Ormeaux                          11
LaSalle, Quebec                              10
Ahuntsic, Quebec                              8
Chomedey, Quebec                              6
Kirkland, Quebec                              5
Parc-Extension, Quebec                        4
Petite-Bourgogne                              4
The Plateau,Montreal                          4
Saint-Pierre, Montreal                        2
Sainte-Geneviève, Quebec                      2
Anjou, Quebec                                 1
Senneville, Quebec                            1

In [198]:
s1[s1["Venue Category"].str.contains('|'.join(searchfor) )]

Neighborhoods  Neighborhood Latitude  Neighborhood Longitude  \
1            Place Bonaventure              45.499583              -73.564917   
2            Place Bonaventure              45.499583              -73.564917   
4            Place Bonaventure              45.499583              -73.564917   
5            Place Bonaventure              45.499583              -73.564917   
8            Place Bonaventure              45.499583              -73.564917   
11           Place Bonaventure              45.499583              -73.564917   
12           Place Bonaventure              45.499583              -73.564917   
15           Place Bonaventure              45.499583              -73.564917   
16           Place Bonaventure              45.499583              -73.564917   
19           Place Bonaventure              45.499583              -73.564917   
20           Place Bonaventure              45.499583              -73.564917   
21           Place Bonaventure              45.499583              -73.564917   
22           Place Bonaventure              45.499583              -73.564917   
24           Place Bonaventure              45.499583              -73.564917   
25           Place Bonaventure              45.499583              -73.564917   
26           Place Bonaventure              45.499583              -73.564917   
27           Place Bonaventure              45.499583              -73.564917   
29           Place Bonaventure              45.499583              -73.564917   
30           Place Bonaventure              45.499583              -73.564917   
31           Place Bonaventure              45.499583              -73.564917   
38         Dollard-des-Ormeaux              45.484230              -73.806455   
41         Dollard-des-Ormeaux              45.484230              -73.806455   
47         Dollard-des-Ormeaux              45.484230              -73.806455   
53         Dollard-des-Ormeaux              45.484230              -73.806455   
56         Dollard-des-Ormeaux              45.484230              -73.806455   
59         Dollard-des-Ormeaux              45.484230              -73.806455   
62         Dollard-des-Ormeaux              45.484230              -73.806455   
68         Dollard-des-Ormeaux              45.484230              -73.806455   
71         Dollard-des-Ormeaux              45.484230              -73.806455   
80         Dollard-des-Ormeaux              45.484230              -73.806455   
83         Dollard-des-Ormeaux              45.484230              -73.806455   
194           Ahuntsic, Quebec              45.559308              -73.652702   
199           Ahuntsic, Quebec              45.559308              -73.652702   
209           Ahuntsic, Quebec              45.559308              -73.652702   
214           Ahuntsic, Quebec              45.559308              -73.652702   
219           Ahuntsic, Quebec              45.559308              -73.652702   
234           Ahuntsic, Quebec              45.559308              -73.652702   
254           Ahuntsic, Quebec              45.559308              -73.652702   
264           Ahuntsic, Quebec              45.559308              -73.652702   
572           Place Desjardins              45.507424              -73.564455   
573           Place Desjardins              45.507424              -73.564455   
574           Place Desjardins              45.507424              -73.564455   
579           Place Desjardins              45.507424              -73.564455   
583           Place Desjardins              45.507424              -73.564455   
584           Place Desjardins              45.507424              -73.564455   
588           Place Desjardins              45.507424              -73.564455   
589           Place Desjardins              45.507424              -73.564455   
590           Place Desjardins              45.507424              -73.564455   
591           Place Desjardins              45.5

Let us map out the different restaurants in these neighborhoods

In [199]:
# create map of Montreal using latitude and longitude values
map_MTL = folium.Map(location=[45.5017, -73.5673], zoom_start=10)

# add markers to map
for lat, lng, neighborhood in zip(s1['Neighborhood Latitude'], s1['Neighborhood Longitude'],  s1['Neighborhoods']):
    label = '{}, '.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_MTL)  
    
map_MTL

Observing the map above, there are 5 neighborhoods that are close to each other. They are Petit Bourgogne, Griffintown, Place Bonaventure, Old Montreal, Place Desjardins

## Conclusion

Throughout the analysis, a list of cities were found that has the most potential for having the greatest culinary experience in Montreal. For tourist, companies, or anyone that want to take advantage of the foodie potential of the area, staying at **Place Desjardins**, **Old Montreal**, **Place Bonaventure** or **Griffintown** is their best bet. With the research, these 4 neighborhoods are concluded to have the most restaurants, and with K-Means, it was determined that restaurants are their most common venue. In addition looking, at the map of Montreal, the top 3 locations are situated near each other. I'd recommend anyone to stay near those 3 neighborhoods to have the upmost experience.

This activity was a fun way to use what we learned to enhanced our skills within the datascience realm. However, I believe the research I have done could've went into more depth by lookign at the different rating as the restaurants. As much as I do believe that the top 4 neighborhoods are neighborgoods that do have many restaurants in Montreal, I think there is missing a lot of data on the different restaurants that is offered at the Plateau. Being a Montreal Native, I'm surprise how many restaurants are missing using the foursquare API and I hope to redo this project using a different API in the future.